- init: Initializes any variables that need to be available during use of the object. It can also run basic functionality to initialize internal methods.

- model: Creates a deep neural network that represents a particular class. In the case of the Discriminator, it's a simple binary classification type neural network.

- summary: This is a simple wrapper for pretty printing the model summary.

- save_model: The function saves a photo of the model structure in this case, it uses the .png format.

The model definition for the discriminator is a binary classifier structure.

The LeakyReLU is a
special kind of activation layer that ensures that small gradients can
be used when the unit is not active. In practice, this is advantageous
over a normal ReLU for ensuring that you have issues with nonactivated
units when the activation approaches zero.

In [1]:
#!/usr/bin/env python3
import sys
import numpy as np
from keras.layers import Input, Dense, Reshape, Flatten, Dropout
from keras.layers.advanced_activations import LeakyReLU
from keras.models import Sequential, Model
from keras.optimizers import Adam
from keras.utils import plot_model

class Discriminator(object):
    def __init__(self, width = 28, height= 28, channels = 1, latent_size=100):
        self.CAPACITY = width*height*channels
        self.SHAPE = (width,height,channels)
        self.OPTIMIZER = Adam(lr=0.0002, decay=8e-9)


        self.Discriminator = self.model()
        self.Discriminator.compile(loss='binary_crossentropy', optimizer=self.OPTIMIZER, metrics=['accuracy'] )
        self.save_model()
        self.summary()

    def model(self):
        model = Sequential()
        model.add(Flatten(input_shape=self.SHAPE))
        model.add(Dense(self.CAPACITY, input_shape=self.SHAPE))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dense(int(self.CAPACITY/2)))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dense(1, activation='sigmoid'))
        return model

    def summary(self):
        return self.Discriminator.summary()

    def save_model(self):
        plot_model(self.Discriminator.model, to_file='/data/Discriminator_Model.png')

Using TensorFlow backend.


In [2]:
from keras.layers import BatchNormalization

class Generator(object):
    def __init__(self, width = 28, height= 28, channels = 1, latent_size=100):
        self.W = width
        self.H = height
        self.C = channels
        self.OPTIMIZER = Adam(lr=0.0002, decay=8e-9)

        self.LATENT_SPACE_SIZE = latent_size
        self.latent_space = np.random.normal(0,1,(self.LATENT_SPACE_SIZE,))

        self.Generator = self.model()
        self.Generator.compile(loss='binary_crossentropy', optimizer=self.OPTIMIZER)
        self.save_model()
        self.summary()

    def model(self, block_starting_size=128,num_blocks=4):
        model = Sequential()
        
        block_size = block_starting_size 
        model.add(Dense(block_size, input_shape=(self.LATENT_SPACE_SIZE,)))
        model.add(LeakyReLU(alpha=0.2))
        model.add(BatchNormalization(momentum=0.8))

        for i in range(num_blocks-1):
            block_size = block_size * 2
            model.add(Dense(block_size))
            model.add(LeakyReLU(alpha=0.2))
            model.add(BatchNormalization(momentum=0.8))

        model.add(Dense(self.W * self.H * self.C, activation='tanh'))
        model.add(Reshape((self.W, self.H, self.C)))
        
        return model

    def summary(self):
        return self.Generator.summary()

    def save_model(self):
        plot_model(self.Generator.model, to_file='/data/Generator_Model.png')

The discriminator then sets its trainability to False, meaning that
during the adversarial training, it will not be training. The generator is
consistently getting better, but the discriminator will remain the same.

in def model(self)

Use a sequential model with the generator as the first piece and the
discriminator as the second. The GAN model will then take in a latent
sample and output a probability regarding whether it belongs to that class
or not.


In [3]:
class GAN(object):
    def __init__(self,discriminator,generator):
        self.OPTIMIZER = Adam(lr=0.0002, decay=8e-9)
        
        self.Generator = generator

        self.Discriminator = discriminator
        self.Discriminator.trainable = False
        
        self.gan_model = self.model()
        self.gan_model.compile(loss='binary_crossentropy', optimizer=self.OPTIMIZER)
        self.save_model()
        self.summary()

    def model(self):
        model = Sequential()
        model.add(self.Generator)
        model.add(self.Discriminator)
        return model

    def summary(self):
        return self.gan_model.summary()

    def save_model(self):
        plot_model(self.gan_model.model, to_file='/data/GAN_Model.png')

The model_type allows us to switch between all of the MNIST digits
(model_type = -1) to a particular digit (model_type = [0,9]).

We'll now train the GAN with mislabeled generator outputs. That
is to say that we will generate images from noise and assign a label
to one of them while training with the GAN. Why? This is the so called
*adversarial* training portion of the training where we are
using the newly trained discriminator to improve the generated
output—the report GAN loss is going to describe the confusion of
the discriminator from the generated outputs

In [7]:
from keras.datasets import mnist
from random import randint
import numpy as np
import matplotlib.pyplot as plt
import os 

os.environ["PATH"] += os.pathsep + 'C:/Program Files (x86)/Graphviz2.38/bin/'

class Trainer:
    def __init__(self, width = 28, height= 28, channels = 1, latent_size=100, epochs =50000, batch=32, checkpoint=50,model_type=-1):
        self.W = width
        self.H = height
        self.C = channels
        self.EPOCHS = epochs
        self.BATCH = batch
        self.CHECKPOINT = checkpoint
        self.model_type=model_type

        self.LATENT_SPACE_SIZE = latent_size

        self.generator = Generator(height=self.H, width=self.W, channels=self.C, latent_size=self.LATENT_SPACE_SIZE)
        self.discriminator = Discriminator(height=self.H, width=self.W, channels=self.C)
        self.gan = GAN(generator=self.generator.Generator, discriminator=self.discriminator.Discriminator)

        self.load_MNIST()

    def load_MNIST(self,model_type=3):
        allowed_types = [-1,0,1,2,3,4,5,6,7,8,9]
        if self.model_type not in allowed_types:
            print('ERROR: Only Integer Values from -1 to 9 are allowed')

        (self.X_train, self.Y_train), (_, _) = mnist.load_data()
        if self.model_type!=-1:
            self.X_train = self.X_train[np.where(self.Y_train==int(self.model_type))[0]]
        
        # Rescale -1 to 1
        # Find Normalize Function from CV Class  
        self.X_train = ( np.float32(self.X_train) - 127.5) / 127.5
        self.X_train = np.expand_dims(self.X_train, axis=3)
        return

    def train(self):
        for e in range(self.EPOCHS):
            # Train Discriminator
            # Make the training batch for this model be half real, half noise
            # Grab Real Images for this training batch
            count_real_images = int(self.BATCH/2)
            starting_index = randint(0, (len(self.X_train)-count_real_images))
            real_images_raw = self.X_train[ starting_index : (starting_index + count_real_images) ]
            x_real_images = real_images_raw.reshape( count_real_images, self.W, self.H, self.C )
            y_real_labels = np.ones([count_real_images,1])

            # Grab Generated Images for this training batch
            latent_space_samples = self.sample_latent_space(count_real_images)
            x_generated_images = self.generator.Generator.predict(latent_space_samples)
            y_generated_labels = np.zeros([self.BATCH-count_real_images,1])

            # Combine to train on the discriminator
            x_batch = np.concatenate( [x_real_images, x_generated_images] )
            y_batch = np.concatenate( [y_real_labels, y_generated_labels] )

            # Now, train the discriminator with this batch
            discriminator_loss = self.discriminator.Discriminator.train_on_batch(x_batch,y_batch)[0]
        
            # Generate Noise => train generator
            x_latent_space_samples = self.sample_latent_space(self.BATCH)
            y_generated_labels = np.ones([self.BATCH,1])
            generator_loss = self.gan.gan_model.train_on_batch(x_latent_space_samples,y_generated_labels)

            print ('Epoch: '+str(int(e))+', [Discriminator :: Loss: '+str(discriminator_loss)+'], [ Generator :: Loss: '+str(generator_loss)+']')
                        
            if e % self.CHECKPOINT == 0 :
                self.plot_checkpoint(e)
        return

    def sample_latent_space(self, instances):
        return np.random.normal(0, 1, (instances,self.LATENT_SPACE_SIZE))

    def plot_checkpoint(self,e):
        filename = "/data/sample_"+str(e)+".png"

        noise = self.sample_latent_space(16)
        images = self.generator.Generator.predict(noise)
        
        plt.figure(figsize=(10,10))
        for i in range(images.shape[0]):
            plt.subplot(4, 4, i+1)
            image = images[i, :, :, :]
            image = np.reshape(image, [self.H,self.W])
            plt.imshow(image, cmap='gray')
            plt.axis('off')
        plt.tight_layout()
        plt.savefig(filename)
        plt.close('all')
        return

In [8]:
t = Trainer()
t.train()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_6 (Dense)              (None, 128)               12928     
_________________________________________________________________
leaky_re_lu_5 (LeakyReLU)    (None, 128)               0         
_________________________________________________________________
batch_normalization_5 (Batch (None, 128)               512       
_________________________________________________________________
dense_7 (Dense)              (None, 256)               33024     
_________________________________________________________________
leaky_re_lu_6 (LeakyReLU)    (None, 256)               0         
_________________________________________________________________
batch_normalization_6 (Batch (None, 256)               1024      
_________________________________________________________________
dense_8 (Dense)              (None, 512)               131584    
__________

C:\Anaconda\envs\tensorflow-gpu\lib\site-packages\keras\engine\training.py:973: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


Epoch: 0, [Discriminator :: Loss: 0.532083], [ Generator :: Loss: 0.784371]
Epoch: 1, [Discriminator :: Loss: 0.337941], [ Generator :: Loss: 0.708861]
Epoch: 2, [Discriminator :: Loss: 0.33921], [ Generator :: Loss: 0.791129]
Epoch: 3, [Discriminator :: Loss: 0.318711], [ Generator :: Loss: 0.805942]
Epoch: 4, [Discriminator :: Loss: 0.307665], [ Generator :: Loss: 0.933077]
Epoch: 5, [Discriminator :: Loss: 0.268409], [ Generator :: Loss: 1.03143]
Epoch: 6, [Discriminator :: Loss: 0.245848], [ Generator :: Loss: 1.06782]
Epoch: 7, [Discriminator :: Loss: 0.210727], [ Generator :: Loss: 1.31962]
Epoch: 8, [Discriminator :: Loss: 0.157593], [ Generator :: Loss: 1.39015]
Epoch: 9, [Discriminator :: Loss: 0.134868], [ Generator :: Loss: 1.61556]
Epoch: 10, [Discriminator :: Loss: 0.126547], [ Generator :: Loss: 1.82047]
Epoch: 11, [Discriminator :: Loss: 0.0978854], [ Generator :: Loss: 1.96227]
Epoch: 12, [Discriminator :: Loss: 0.0910214], [ Generator :: Loss: 2.14366]
Epoch: 13, [Disc

Epoch: 108, [Discriminator :: Loss: 0.00405479], [ Generator :: Loss: 5.63179]
Epoch: 109, [Discriminator :: Loss: 0.00713879], [ Generator :: Loss: 5.49348]
Epoch: 110, [Discriminator :: Loss: 0.00432459], [ Generator :: Loss: 5.41072]
Epoch: 111, [Discriminator :: Loss: 0.00559204], [ Generator :: Loss: 5.53946]
Epoch: 112, [Discriminator :: Loss: 0.00383107], [ Generator :: Loss: 5.34935]
Epoch: 113, [Discriminator :: Loss: 0.00758455], [ Generator :: Loss: 5.65741]
Epoch: 114, [Discriminator :: Loss: 0.0051267], [ Generator :: Loss: 5.31953]
Epoch: 115, [Discriminator :: Loss: 0.00729723], [ Generator :: Loss: 5.55236]
Epoch: 116, [Discriminator :: Loss: 0.00202808], [ Generator :: Loss: 5.37154]
Epoch: 117, [Discriminator :: Loss: 0.00791604], [ Generator :: Loss: 5.57953]
Epoch: 118, [Discriminator :: Loss: 0.00608496], [ Generator :: Loss: 5.49037]
Epoch: 119, [Discriminator :: Loss: 0.00279413], [ Generator :: Loss: 5.35828]
Epoch: 120, [Discriminator :: Loss: 0.00430744], [ Ge

Epoch: 216, [Discriminator :: Loss: 0.1534], [ Generator :: Loss: 5.70269]
Epoch: 217, [Discriminator :: Loss: 0.0665893], [ Generator :: Loss: 6.60372]
Epoch: 218, [Discriminator :: Loss: 0.0803479], [ Generator :: Loss: 7.29799]
Epoch: 219, [Discriminator :: Loss: 0.106125], [ Generator :: Loss: 6.97498]
Epoch: 220, [Discriminator :: Loss: 0.408302], [ Generator :: Loss: 6.0987]
Epoch: 221, [Discriminator :: Loss: 0.0519212], [ Generator :: Loss: 5.19289]
Epoch: 222, [Discriminator :: Loss: 0.13378], [ Generator :: Loss: 4.63042]
Epoch: 223, [Discriminator :: Loss: 0.575219], [ Generator :: Loss: 5.15918]
Epoch: 224, [Discriminator :: Loss: 0.264908], [ Generator :: Loss: 5.73208]
Epoch: 225, [Discriminator :: Loss: 0.180673], [ Generator :: Loss: 5.5564]
Epoch: 226, [Discriminator :: Loss: 0.189589], [ Generator :: Loss: 6.43625]
Epoch: 227, [Discriminator :: Loss: 0.087541], [ Generator :: Loss: 7.70849]
Epoch: 228, [Discriminator :: Loss: 0.311485], [ Generator :: Loss: 6.40951]
E

...

Epoch: 49485, [Discriminator :: Loss: 0.512455], [ Generator :: Loss: 1.6614]
Epoch: 49486, [Discriminator :: Loss: 0.517613], [ Generator :: Loss: 1.73194]
Epoch: 49487, [Discriminator :: Loss: 0.306698], [ Generator :: Loss: 2.06299]
Epoch: 49488, [Discriminator :: Loss: 0.466208], [ Generator :: Loss: 2.00888]
Epoch: 49489, [Discriminator :: Loss: 0.528967], [ Generator :: Loss: 1.94521]
Epoch: 49490, [Discriminator :: Loss: 0.534525], [ Generator :: Loss: 1.20941]
Epoch: 49491, [Discriminator :: Loss: 0.588526], [ Generator :: Loss: 0.857341]
Epoch: 49492, [Discriminator :: Loss: 0.319203], [ Generator :: Loss: 0.953786]
Epoch: 49493, [Discriminator :: Loss: 0.432318], [ Generator :: Loss: 0.940273]
Epoch: 49494, [Discriminator :: Loss: 0.446848], [ Generator :: Loss: 1.10941]
Epoch: 49495, [Discriminator :: Loss: 0.475982], [ Generator :: Loss: 1.97486]
Epoch: 49496, [Discriminator :: Loss: 0.394662], [ Generator :: Loss: 2.07644]
Epoch: 49497, [Discriminator :: Loss: 0.413411], [

Epoch: 49591, [Discriminator :: Loss: 0.570524], [ Generator :: Loss: 1.05791]
Epoch: 49592, [Discriminator :: Loss: 0.463638], [ Generator :: Loss: 1.02254]
Epoch: 49593, [Discriminator :: Loss: 0.539508], [ Generator :: Loss: 0.971452]
Epoch: 49594, [Discriminator :: Loss: 0.382826], [ Generator :: Loss: 1.07252]
Epoch: 49595, [Discriminator :: Loss: 0.471381], [ Generator :: Loss: 1.5823]
Epoch: 49596, [Discriminator :: Loss: 0.643831], [ Generator :: Loss: 2.03107]
Epoch: 49597, [Discriminator :: Loss: 0.601353], [ Generator :: Loss: 1.90515]
Epoch: 49598, [Discriminator :: Loss: 0.599482], [ Generator :: Loss: 1.75443]
Epoch: 49599, [Discriminator :: Loss: 0.326074], [ Generator :: Loss: 1.64878]
Epoch: 49600, [Discriminator :: Loss: 0.479786], [ Generator :: Loss: 1.50306]
Epoch: 49601, [Discriminator :: Loss: 0.347372], [ Generator :: Loss: 1.52792]
Epoch: 49602, [Discriminator :: Loss: 0.330295], [ Generator :: Loss: 1.76955]
Epoch: 49603, [Discriminator :: Loss: 0.646312], [ G

Epoch: 49696, [Discriminator :: Loss: 0.346692], [ Generator :: Loss: 1.30318]
Epoch: 49697, [Discriminator :: Loss: 0.364906], [ Generator :: Loss: 1.29267]
Epoch: 49698, [Discriminator :: Loss: 0.620687], [ Generator :: Loss: 1.59887]
Epoch: 49699, [Discriminator :: Loss: 0.312899], [ Generator :: Loss: 1.6492]
Epoch: 49700, [Discriminator :: Loss: 0.3681], [ Generator :: Loss: 1.93267]
Epoch: 49701, [Discriminator :: Loss: 0.363482], [ Generator :: Loss: 2.06186]
Epoch: 49702, [Discriminator :: Loss: 0.44209], [ Generator :: Loss: 1.9171]
Epoch: 49703, [Discriminator :: Loss: 0.402723], [ Generator :: Loss: 1.60128]
Epoch: 49704, [Discriminator :: Loss: 0.457939], [ Generator :: Loss: 1.4092]
Epoch: 49705, [Discriminator :: Loss: 0.42861], [ Generator :: Loss: 1.20822]
Epoch: 49706, [Discriminator :: Loss: 0.598842], [ Generator :: Loss: 0.926064]
Epoch: 49707, [Discriminator :: Loss: 0.5213], [ Generator :: Loss: 1.42725]
Epoch: 49708, [Discriminator :: Loss: 0.352521], [ Generator

Epoch: 49801, [Discriminator :: Loss: 0.516033], [ Generator :: Loss: 1.81622]
Epoch: 49802, [Discriminator :: Loss: 0.443457], [ Generator :: Loss: 1.94994]
Epoch: 49803, [Discriminator :: Loss: 0.465561], [ Generator :: Loss: 1.60018]
Epoch: 49804, [Discriminator :: Loss: 0.368249], [ Generator :: Loss: 1.69101]
Epoch: 49805, [Discriminator :: Loss: 0.347914], [ Generator :: Loss: 1.08792]
Epoch: 49806, [Discriminator :: Loss: 0.444641], [ Generator :: Loss: 0.973322]
Epoch: 49807, [Discriminator :: Loss: 0.407348], [ Generator :: Loss: 0.982144]
Epoch: 49808, [Discriminator :: Loss: 0.5119], [ Generator :: Loss: 1.52834]
Epoch: 49809, [Discriminator :: Loss: 0.408884], [ Generator :: Loss: 1.77229]
Epoch: 49810, [Discriminator :: Loss: 0.455732], [ Generator :: Loss: 1.74338]
Epoch: 49811, [Discriminator :: Loss: 0.483828], [ Generator :: Loss: 2.1428]
Epoch: 49812, [Discriminator :: Loss: 0.480744], [ Generator :: Loss: 1.67699]
Epoch: 49813, [Discriminator :: Loss: 0.396814], [ Ge

Epoch: 49906, [Discriminator :: Loss: 0.497221], [ Generator :: Loss: 1.51469]
Epoch: 49907, [Discriminator :: Loss: 0.431595], [ Generator :: Loss: 1.56308]
Epoch: 49908, [Discriminator :: Loss: 0.529193], [ Generator :: Loss: 1.45109]
Epoch: 49909, [Discriminator :: Loss: 0.659108], [ Generator :: Loss: 1.86472]
Epoch: 49910, [Discriminator :: Loss: 0.540466], [ Generator :: Loss: 1.67607]
Epoch: 49911, [Discriminator :: Loss: 0.376645], [ Generator :: Loss: 1.85106]
Epoch: 49912, [Discriminator :: Loss: 0.518931], [ Generator :: Loss: 1.84148]
Epoch: 49913, [Discriminator :: Loss: 0.419042], [ Generator :: Loss: 1.33202]
Epoch: 49914, [Discriminator :: Loss: 0.462794], [ Generator :: Loss: 1.42874]
Epoch: 49915, [Discriminator :: Loss: 0.507723], [ Generator :: Loss: 1.32681]
Epoch: 49916, [Discriminator :: Loss: 0.581804], [ Generator :: Loss: 1.26783]
Epoch: 49917, [Discriminator :: Loss: 0.458421], [ Generator :: Loss: 1.54306]
Epoch: 49918, [Discriminator :: Loss: 0.346066], [ G